# Aplicación para Obtener Comentarios de Reddit - SpainPolitics

Esta aplicación obtiene todos los comentarios del subreddit SpainPolitics de los últimos 5 meses.

In [7]:
# Instalar praw si no está instalado
import subprocess
import sys

try:
    import praw
    print("PRAW ya está instalado")
except ImportError:
    print("Instalando PRAW...")
    subprocess.check_call([sys.executable, "-m", "pip", "install", "praw"])
    import praw
    print("PRAW instalado correctamente")

# Importar librerías necesarias
import pandas as pd
from datetime import datetime, timedelta
import time
import json

PRAW ya está instalado


In [ ]:
# Configuración de Reddit API
# Para usar esta aplicación necesitas crear una app en Reddit:
# 1. Ve a https://www.reddit.com/prefs/apps/
# 2. Haz clic en "Create App" o "Create Another App"
# 3. Nombre: SpainPoliticsComments
# 4. Tipo: script
# 5. Description: Obtener comentarios de SpainPolitics
# 6. About URL: (deja en blanco)
# 7. Redirect URI: http://localhost:8080

# IMPORTANTE: Reemplaza estos valores con los de tu aplicación de Reddit
REDDIT_CLIENT_ID = "your_reddit_client_ID"  # El ID que aparece bajo el nombre de tu app
REDDIT_CLIENT_SECRET = "your_reddit_client_secret"  # El secret de tu app (sin espacios)
REDDIT_USER_AGENT = "your_reddit_user_agent"  

# Configuración de búsqueda
SUBREDDIT_NAME = "SpainEconomics"

print("  Configuración actualizada:")
print(f"   Client ID: {REDDIT_CLIENT_ID}")
print(f"   Client Secret: {'*' * len(REDDIT_CLIENT_SECRET)}")
print(f"   User Agent: {REDDIT_USER_AGENT}")
print(f"   Subreddit: {SUBREDDIT_NAME}")

🔧 Configuración actualizada:
   Client ID: kqbngN8T-2EXVkoMdULgTA
   Client Secret: ******************************
   User Agent: SpainPoliticsComments/1.0 by /u/Guardian4224
   Subreddit: SpainEconomics
   Meses atrás: 6


In [ ]:
def obtener_comentarios_reddit_rango_fechas(subreddit_name, fecha_inicio, fecha_fin, max_posts=1000, max_comments_per_post=200):
    """
    Versión optimizada para obtener comentarios en un rango de fechas específico
    """
    try:
        # Limpiar credenciales
        client_id = REDDIT_CLIENT_ID.strip()
        client_secret = REDDIT_CLIENT_SECRET.strip()
        user_agent = REDDIT_USER_AGENT.strip()
        
        print("Configuración:")
        print(f" Desde: {fecha_inicio}")
        print(f" Hasta: {fecha_fin}")
        print(f" Máximo posts: {max_posts}")
        print(f" Máximo comentarios por post: {max_comments_per_post}")
        
        # Inicializar Reddit
        reddit = praw.Reddit(
            client_id=client_id,
            client_secret=client_secret,
            user_agent=user_agent
        )
        
        print(f"🔍 Conectando a r/{subreddit_name}...")
        subreddit = reddit.subreddit(subreddit_name)
        
        # Convertir fechas a timestamps
        fecha_inicio_timestamp = datetime.strptime(fecha_inicio, "%Y-%m-%d").timestamp()
        fecha_fin_timestamp = datetime.strptime(fecha_fin, "%Y-%m-%d").timestamp()
        
        comentarios_data = []
        posts_procesados = 0
        comentarios_encontrados = 0
        posts_en_rango = 0
        
        print("Obteniendo posts...")
        print(f"Buscando posts entre {fecha_inicio} y {fecha_fin}")
        
        # Buscar en diferentes ordenamientos para maximizar la cobertura
        post_sources = [
            ('new', subreddit.new(limit=max_posts)),
            ('hot', subreddit.hot(limit=max_posts//2)),
            ('top_year', subreddit.top('year', limit=max_posts//2))
        ]
        
        posts_procesados_total = set()  # Para evitar duplicados
        
        for source_name, post_source in post_sources:
            print(f"Procesando posts de '{source_name}'...")
            
            for post in post_source:
                if post.id in posts_procesados_total:
                    continue  # Evitar duplicados
                
                posts_procesados_total.add(post.id)
                posts_procesados += 1
                
                # Verificar si el post está en el rango de fechas
                if not (fecha_inicio_timestamp <= post.created_utc <= fecha_fin_timestamp):
                    continue
                
                posts_en_rango += 1
                
                try:
                    # OPTIMIZACIÓN: Limitar comentarios expandidos
                    post.comments.replace_more(limit=5)  # Solo expande 5 niveles en lugar de todos
                    
                    comments_processed_in_post = 0
                    for comment in post.comments.list():
                        # Límite por post para no procesar posts con miles de comentarios
                        if comments_processed_in_post >= max_comments_per_post:
                            break
                        
                        # Verificar si el comentario está en el rango de fechas
                        if not (fecha_inicio_timestamp <= comment.created_utc <= fecha_fin_timestamp):
                            continue
                        
                        comentarios_encontrados += 1
                        comments_processed_in_post += 1
                        
                        comentarios_data.append({
                            'id': comment.id,
                            'post_id': post.id,
                            'post_title': post.title,
                            'comment_text': comment.body,
                            'author': str(comment.author) if comment.author else '[deleted]',
                            'score': comment.score,
                            'created_utc': comment.created_utc,
                            'created_date': datetime.utcfromtimestamp(comment.created_utc).isoformat(),
                            'permalink': f"https://reddit.com{comment.permalink}",
                            'subreddit': subreddit_name
                        })
                        
                        # Progreso cada 50 comentarios
                        if comentarios_encontrados % 50 == 0:
                            print(f"{comentarios_encontrados} comentarios encontrados...")
                    
                except Exception as e:
                    print(f"Error en post {posts_procesados}: {str(e)[:50]}...")
                    continue
                
                # Progreso cada 10 posts
                if posts_procesados % 10 == 0:
                    print(f" {posts_procesados} posts procesados, {comentarios_encontrados} comentarios encontrados")
                
                time.sleep(0.1) 
        
        print(f"Proceso completado!")
        print(f"Posts totales procesados: {posts_procesados}")
        print(f"Posts en rango de fechas: {posts_en_rango}")
        print(f"Comentarios encontrados: {comentarios_encontrados}")
        
        return pd.DataFrame(comentarios_data)
        
    except Exception as e:
        print(f"Error: {str(e)}")
        return pd.DataFrame()

In [ ]:
from datetime import datetime

# Período: desde 2022-01-01 hasta la fecha actual
FECHA_INICIO = "2022-01-01"
FECHA_FIN = datetime.utcnow().date().isoformat()  # Fecha de hoy (UTC)

# Límites razonables para cubrir el período sin tardar demasiado
MAX_POSTS = 100000
MAX_COMMENTS_PER_POST = 500

print(f"Configuración:")
print(f"Subreddit: {SUBREDDIT_NAME}")
print(f"Desde: {FECHA_INICIO}")
print(f"Hasta: {FECHA_FIN}")
print(f"Máximo posts: {MAX_POSTS}")
print(f"Máximo comentarios por post: {MAX_COMMENTS_PER_POST}")
print()

# Ejecutar extracción en el rango indicado
df_comentarios_rapido = obtener_comentarios_reddit_rango_fechas(
    SUBREDDIT_NAME,
    FECHA_INICIO,
    FECHA_FIN,
    MAX_POSTS,
    MAX_COMMENTS_PER_POST
)

# Mostrar y guardar resultados
if not df_comentarios_rapido.empty:
    print(f"\RESULTADOS:")
    print(f"Total de comentarios: {len(df_comentarios_rapido)}")
    print(f"Fecha más antigua: {df_comentarios_rapido['created_date'].min()}")
    print(f"Fecha más reciente: {df_comentarios_rapido['created_date'].max()}")
    print(f"Autores únicos: {df_comentarios_rapido['author'].nunique()}")
    print(f"Posts únicos: {df_comentarios_rapido['post_id'].nunique()}")

    # Guardar CSV y JSON con el rango en el nombre
    archivo_csv = f"comentarios_{SUBREDDIT_NAME}_{FECHA_INICIO}_to_{FECHA_FIN}.csv"
    archivo_json = f"comentarios_{SUBREDDIT_NAME}_{FECHA_INICIO}_to_{FECHA_FIN}.json"
    df_comentarios_rapido.to_csv(archivo_csv, index=False, encoding='utf-8')
    df_comentarios_rapido.to_json(archivo_json, orient='records', indent=2, force_ascii=False)
    print(f"Guardado en: {archivo_csv}")
    print(f"Guardado en: {archivo_json}")
else:
    print("\nNo se encontraron comentarios en el rango especificado o ocurrió un error.")

🚀 EXTRACCIÓN DE COMENTARIOS (2023-01-01 → HOY)
⚡ Configuración:
   Subreddit: SpainEconomics
   Desde: 2022-01-01
   Hasta: 2025-10-12
   Máximo posts: 100000
   Máximo comentarios por post: 500

🚀 VERSIÓN RANGO DE FECHAS - Configuración:
   📅 Desde: 2022-01-01
   📅 Hasta: 2025-10-12
   📝 Máximo posts: 100000
   💬 Máximo comentarios por post: 500
🔍 Conectando a r/SpainEconomics...
📖 Obteniendo posts...
   🎯 Buscando posts entre 2022-01-01 y 2025-10-12
   📋 Procesando posts de 'new'...


C:\Users\Alonso\AppData\Local\Temp\ipykernel_19012\957666304.py:44: DeprecationWarning: Positional arguments for 'BaseListingMixin.top' will no longer be supported in PRAW 8.
Call this function with 'time_filter' as a keyword argument.
  ('top_year', subreddit.top('year', limit=max_posts//2))


   💬 50 comentarios encontrados...
   📝 10 posts procesados, 98 comentarios encontrados
   📝 10 posts procesados, 98 comentarios encontrados
   💬 100 comentarios encontrados...
   💬 100 comentarios encontrados...
   💬 150 comentarios encontrados...
   💬 150 comentarios encontrados...
   💬 200 comentarios encontrados...
   💬 250 comentarios encontrados...
   💬 300 comentarios encontrados...
   💬 200 comentarios encontrados...
   💬 250 comentarios encontrados...
   💬 300 comentarios encontrados...
   💬 350 comentarios encontrados...
   💬 400 comentarios encontrados...
   💬 350 comentarios encontrados...
   💬 400 comentarios encontrados...
   💬 450 comentarios encontrados...
   💬 500 comentarios encontrados...
   📝 20 posts procesados, 537 comentarios encontrados
   💬 450 comentarios encontrados...
   💬 500 comentarios encontrados...
   📝 20 posts procesados, 537 comentarios encontrados
   💬 550 comentarios encontrados...
   💬 550 comentarios encontrados...
   💬 600 comentarios encontrado

In [27]:
# Leemos el CSV y nos disponemos a procesarlo

import pandas as pd
df = pd.read_csv("comentarios_SpainEconomics_2022-01-01_to_2025-10-12.csv")

# Eliminamos columnas que finalmente pensamos innecesarias
cols_to_drop = ["subreddit", "author", "created_utc"]

df.drop(cols_to_drop, axis=1, inplace=True)

In [28]:
# Añadimos un ID único a cada comentario, manteniendo el permalink para mantener la rastreabilidad

import uuid
df['id'] = df.apply(lambda _: str(uuid.uuid4()), axis=1)
df

id  post_id  \
0      6049524d-7f68-4a5e-90d4-c54882c475b0  1o3xexz   
1      00e3ee5d-49ec-4f5e-89fa-646087353a1b  1o3xexz   
2      5d3d5943-3555-4540-8945-f375dc93e0ea  1o3xexz   
3      b03279a5-28d0-4328-b2b0-690f20abc2f1  1o3xexz   
4      f69de5a4-1991-4f81-8a3e-64dcf2639d7d  1o3xexz   
...                                     ...      ...   
38721  f90fe8e3-6357-410e-9ea2-61d0d1e8325c  1gbmxvo   
38722  96148381-bfe5-4119-9fbc-33de97d3cf51  1gbmxvo   
38723  b0812ef7-608e-4e85-90b7-b3d6e41c28c2  1gbmxvo   
38724  abaf16a9-0db2-4dca-aac8-f8edb925001f  1gbmxvo   
38725  2b5458fa-89b6-4729-ad7f-439b82e4a79d  1gbmxvo   

                                              post_title  \
0      La construcción de vivienda protegida para alq...   
1      La construcción de vivienda protegida para alq...   
2      La construcción de vivienda protegida para alq...   
3      La construcción de vivienda protegida para alq...   
4      La construcción de vivienda protegida para alq...   
...                                                  ...   
38721  El fracaso del SEPE: la empresa familiar coloc...   
38722  El fracaso del SEPE: la empresa familiar coloc...   
38723  El fracaso del SEPE: la empresa familiar coloc...   
38724  El fracaso del SEPE: la empresa familiar coloc...   
38725  El fracaso del SEPE: la empresa familiar coloc...   

                                            comment_text  score  \
0      Decir que 5000 es que se dispara... Efecto bas...     27   
1      ¿Para alquiler de por vida? ¿Siempre propiedad...     13   
2      "si no es exactamente como yo quiero, que no s...     -4   
3      ¿Estás a favor de que la vivienda protegida se...     15   
4      Estoy a favor de que se construya vivienda pro...     -4   
...                                                  ...    ...   
38721  En tu mundo "real" todo el mundo es un sinverg...      1   
38722  En la vIda recoges los que siembras.\n\nDespué...      2   
38723               Como el mercado de la vivienda?\n\n😂      1   
38724  Pues el título debería servir como base. Ya a ...      1   
38725  El problema de eso es que ahora todos tienen u...      1   

              created_date                                          permalink  
0      2025-10-11T19:02:53  https://reddit.com/r/SpainEconomics/comments/1...  
1      2025-10-11T15:12:00  https://reddit.com/r/SpainEconomics/comments/1...  
2      2025-10-11T18:13:40  https://reddit.com/r/SpainEconomics/comments/1...  
3      2025-10-11T19:18:32  https://reddit.com/r/SpainEconomics/comments/1...  
4      2025-10-11T19:21:44  https://reddit.com/r/SpainEconomics/comments/1...  
...                    ...                                                ...  
38721  2024-10-25T20:15:56  https://reddit.com/r/SpainEconomics/comments/1...  
38722  2024-10-25T21:08:18  https://reddit.com/r/SpainEconomics/comments/1...  
38723  2024-10-25T21:10:02  https://reddit.com/r/SpainEconomics/comments/1...  
38724  2024-10-26T19:21:09  https://reddit.com/r/SpainEconomics/comments/1...  
38725  2024-10-27T16:19:21  https://reddit.com/r/SpainEconomics/comments/1...  

[38726 rows x 7 columns]

In [29]:
# Unimos los textos en una única columna
df['text'] = df['post_title'].astype(str) + '\n\n' + df['comment_text'].astype(str)

df.drop(['post_title', 'comment_text'], axis=1, inplace=True)
df

id  post_id  score  \
0      6049524d-7f68-4a5e-90d4-c54882c475b0  1o3xexz     27   
1      00e3ee5d-49ec-4f5e-89fa-646087353a1b  1o3xexz     13   
2      5d3d5943-3555-4540-8945-f375dc93e0ea  1o3xexz     -4   
3      b03279a5-28d0-4328-b2b0-690f20abc2f1  1o3xexz     15   
4      f69de5a4-1991-4f81-8a3e-64dcf2639d7d  1o3xexz     -4   
...                                     ...      ...    ...   
38721  f90fe8e3-6357-410e-9ea2-61d0d1e8325c  1gbmxvo      1   
38722  96148381-bfe5-4119-9fbc-33de97d3cf51  1gbmxvo      2   
38723  b0812ef7-608e-4e85-90b7-b3d6e41c28c2  1gbmxvo      1   
38724  abaf16a9-0db2-4dca-aac8-f8edb925001f  1gbmxvo      1   
38725  2b5458fa-89b6-4729-ad7f-439b82e4a79d  1gbmxvo      1   

              created_date                                          permalink  \
0      2025-10-11T19:02:53  https://reddit.com/r/SpainEconomics/comments/1...   
1      2025-10-11T15:12:00  https://reddit.com/r/SpainEconomics/comments/1...   
2      2025-10-11T18:13:40  https://reddit.com/r/SpainEconomics/comments/1...   
3      2025-10-11T19:18:32  https://reddit.com/r/SpainEconomics/comments/1...   
4      2025-10-11T19:21:44  https://reddit.com/r/SpainEconomics/comments/1...   
...                    ...                                                ...   
38721  2024-10-25T20:15:56  https://reddit.com/r/SpainEconomics/comments/1...   
38722  2024-10-25T21:08:18  https://reddit.com/r/SpainEconomics/comments/1...   
38723  2024-10-25T21:10:02  https://reddit.com/r/SpainEconomics/comments/1...   
38724  2024-10-26T19:21:09  https://reddit.com/r/SpainEconomics/comments/1...   
38725  2024-10-27T16:19:21  https://reddit.com/r/SpainEconomics/comments/1...   

                                                    text  
0      La construcción de vivienda protegida para alq...  
1      La construcción de vivienda protegida para alq...  
2      La construcción de vivienda protegida para alq...  
3      La construcción de vivienda protegida para alq...  
4      La construcción de vivienda protegida para alq...  
...                                                  ...  
38721  El fracaso del SEPE: la empresa familiar coloc...  
38722  El fracaso del SEPE: la empresa familiar coloc...  
38723  El fracaso del SEPE: la empresa familiar coloc...  
38724  El fracaso del SEPE: la empresa familiar coloc...  
38725  El fracaso del SEPE: la empresa familiar coloc...  

[38726 rows x 6 columns]

In [30]:
# Reordenamos columnas para mayor claridad y renombramos 'created_date' a 'timestamp'
df = df.rename(columns={'created_date': 'timestamp'})
df = df[['id', 'post_id', 'text', 'score', 'timestamp', 'permalink']]
df

id  post_id  \
0      6049524d-7f68-4a5e-90d4-c54882c475b0  1o3xexz   
1      00e3ee5d-49ec-4f5e-89fa-646087353a1b  1o3xexz   
2      5d3d5943-3555-4540-8945-f375dc93e0ea  1o3xexz   
3      b03279a5-28d0-4328-b2b0-690f20abc2f1  1o3xexz   
4      f69de5a4-1991-4f81-8a3e-64dcf2639d7d  1o3xexz   
...                                     ...      ...   
38721  f90fe8e3-6357-410e-9ea2-61d0d1e8325c  1gbmxvo   
38722  96148381-bfe5-4119-9fbc-33de97d3cf51  1gbmxvo   
38723  b0812ef7-608e-4e85-90b7-b3d6e41c28c2  1gbmxvo   
38724  abaf16a9-0db2-4dca-aac8-f8edb925001f  1gbmxvo   
38725  2b5458fa-89b6-4729-ad7f-439b82e4a79d  1gbmxvo   

                                                    text  score  \
0      La construcción de vivienda protegida para alq...     27   
1      La construcción de vivienda protegida para alq...     13   
2      La construcción de vivienda protegida para alq...     -4   
3      La construcción de vivienda protegida para alq...     15   
4      La construcción de vivienda protegida para alq...     -4   
...                                                  ...    ...   
38721  El fracaso del SEPE: la empresa familiar coloc...      1   
38722  El fracaso del SEPE: la empresa familiar coloc...      2   
38723  El fracaso del SEPE: la empresa familiar coloc...      1   
38724  El fracaso del SEPE: la empresa familiar coloc...      1   
38725  El fracaso del SEPE: la empresa familiar coloc...      1   

                 timestamp                                          permalink  
0      2025-10-11T19:02:53  https://reddit.com/r/SpainEconomics/comments/1...  
1      2025-10-11T15:12:00  https://reddit.com/r/SpainEconomics/comments/1...  
2      2025-10-11T18:13:40  https://reddit.com/r/SpainEconomics/comments/1...  
3      2025-10-11T19:18:32  https://reddit.com/r/SpainEconomics/comments/1...  
4      2025-10-11T19:21:44  https://reddit.com/r/SpainEconomics/comments/1...  
...                    ...                                                ...  
38721  2024-10-25T20:15:56  https://reddit.com/r/SpainEconomics/comments/1...  
38722  2024-10-25T21:08:18  https://reddit.com/r/SpainEconomics/comments/1...  
38723  2024-10-25T21:10:02  https://reddit.com/r/SpainEconomics/comments/1...  
38724  2024-10-26T19:21:09  https://reddit.com/r/SpainEconomics/comments/1...  
38725  2024-10-27T16:19:21  https://reddit.com/r/SpainEconomics/comments/1...  

[38726 rows x 6 columns]

In [32]:
df.to_csv("SpanishEconomyRedditComments.csv", index=False, encoding='utf-8')